# Atelier DAY 1 :  scorer une variable bimodale

L’objectif de cet atelier est de construire un score pour une variable $Y$ binaire. 
Les use-cases les plus fréquents sont

- score de defaut - banque : $Y$ est l'indicatrice qui indique si la personne a fait défaut ou non
- score de churn - télécom / edf : $Y$ est l'indicatrice qui indique si la personne a résilié son contrat ou non
- score d'appétence - e-commerce : $Y$ est l'indicatrice qui indique si la personne a acheté le produit ou non

Comme usuellement en Data Science, nous distinguons deux grandes phases

### Exploration 

- **Les préliminaires** :  contiennent tout ce dont on a besoin de définir pour faire passer le code : les librairies, les chemins, etc.

- **L’import et l’audit des data** : vérification rapide du contenu du fichier de travail. Permet d’avoir une idée des méthodologies possibles ou impossibles à utiliser. Ici, utilisation d’une régression logistique pour expliquer la variable cible $Y$.

- **L’analyse exploratoire et le  pré-traitement des données** :  construction de dummies ...et cetera

- **Sauvegarde de la base de travail** 

### Modelisation 

- **La modélisation** : constitution de la base LEARN et de la base TEST + recherche d’un bon modèle logistique ==> sélection des variables. 

- **L’évaluation des performances** : courbe ROC + indicateurs AUC, GINI. Sur la base LEARN et TEST.

# Table des matières

[1. Préliminaires ](#basics)<br>
[2. Bases de travail ](#data)<br>
[3. Modélisation ](#model)<br>
[4. Performance](#perf)<br>

<a id='basics'></a>
# 1. Préliminaires

On commence par télécharger le jeu de données

In [ ]:
import requests
import os

url = 'https://stephanegaiffas.github.io/files/formation_cnrs/day1_score.csv.gz'
r = requests.get(url)

# Votre chemin. Par defaut celui du notebook
path_data = '../data/'             
with open(os.path.join(path_data, 'day1_score.csv.gz'), 'wb') as f:
    f.write(r.content)

In [ ]:
import numpy as np
import pandas as pd

df = pd.read_csv(os.path.join(path_data, 'day1_score.csv.gz'), sep=';')
df.shape

In [ ]:
# Regardons les premières lignes du dataframe
df.head()

In [ ]:
# Quelques stats descriptives, quantitatives et qualitatives, met des NaN si incongru.
df.describe(include='all')

### Exercice
Observons la colonne $X1$ : y-a-t-il un problème ? Regardons la première valeur prise par $X1$. 

In [ ]:
df.loc[0, 'X1']

### Exercice
- Que constaste-t-on ? 
- Quel est le type de chacune des variables ?

In [ ]:
# Description IT des données
df.info() 

### Exercice
Il y a eu un problème dans l'import => lequel ? quelle solution ?

In [ ]:
#Import en spécifiant le symbole pour les décimaux 

df = pd.read_csv(os.path.join(path_data, 'day1_score.csv.gz'), sep=';', decimal=',')

# On passe le nom des colonnes en minuscules
df.columns = [x.lower() for x in df.columns]
df.describe(include='all')

In [ ]:
# Identification selon le type de variable
defaut = df['y']
quanti = df.iloc[:, 1:11]
quali = df.iloc[:, 11:21]

print(quanti.columns)
print(quali.columns)
print('-' * 16)

for colname, col in quali.items():
    print(colname + ':')
    print(col.value_counts())
    print('-' * 16)

### Exercice
- Quelles sont les valeurs prises par les quali ?
- Par quoi les coder ?

In [ ]:
# Calculons le taux de cible
tx_cible = defaut.mean()
# Affichons le taux de cible plus joliment
print("Taux de cible: {taux:.2f}%".format(taux=100 * tx_cible))

In [ ]:
# calculs des effectifs 
defaut.value_counts()

<a id='data'></a>
# 2. Bases de travail

Les données brutes (même après nettoyage / data management) nécessitent d'être transformées selon l'objectif. 
Parmi une multitude de choix possibles, nous proposons quatre méthodologies (à challenger entre elles)

- codage des quali / quanti inchangées
- dummies pour les quali / quanti inchangées
- dummies pour les quali et normalisation des quanti
- dummies pour quali ET quanti

## 2.1. Première base de travail : codage des qualitatives 

- Sera sauvée dans un fichier `df_brut.pkl`


In [ ]:
# Codage des quali en nombre
cod = quali.copy()
cod.replace({'A': 1, 'B': 2, 'C': 3, 'D': 4}, inplace=True)

# Rajouter les qualitatives 
df_trav = pd.concat([quanti, cod], axis=1)
df_trav.head()

In [ ]:
import pickle as pkl

path_travail = './'
df_pkl = {'features': df_trav, 'labels': defaut}

with open(os.path.join(path_travail, 'df_brut.pkl'), 'wb') as f:
    pkl.dump(df_pkl, f)

## 2.2. Deuxième base de travail : création de dummies à partir des qualitatives

- Sera sauvée dans un fichier `df_dum.pkl`

In [ ]:
df_trav = pd.get_dummies(df.iloc[:, 1:], drop_first=True)
df_trav.head()

In [ ]:
# Sauver 
with open(os.path.join(path_travail, 'df_dum.pkl'), 'wb') as f:
    pkl.dump({'features': df_trav, 'labels': defaut}, f)

## 2.3. Troisème base de travail : normalisation des variables quanti

- Sera sauvée dans un fichier `df_dumN.pkl`

In [ ]:
quanti.agg({'var', 'max'})

### Exercice
- Qu'observe-t-on ? En particulier sur $x1,x7$ et $x10$. Comment remédier à cet inconvénient ?

In [ ]:
# Reduction des variables quanti
from sklearn.preprocessing import StandardScaler

sc = StandardScaler()
quantiN = pd.DataFrame(sc.fit_transform(quanti), columns=quanti.columns)
quantiN.describe(percentiles=[0.5])

### Exercice
- Que valent les moyennes des nouvelles variables ? les variances ?

In [ ]:
# Put back the "dummied" categorical variables
df_trav = pd.concat([quantiN, quali], axis=1)
df_trav = pd.get_dummies(df_trav, drop_first=True)
df_trav.head()

In [ ]:
# Sauver
with open(os.path.join(path_travail, 'df_dumN.pkl'), 'wb') as f:
    pkl.dump({'features': df_trav, 'labels': defaut}, f)

## 2.4. Quatrième base de travail : dummies pour toutes les variables

- Sera sauvée dans un fichier `df_dumAll.pkl`

In [ ]:
import seaborn as sns

nom = 'x1'
#grid = sns.FacetGrid(hue='y', data=df, height=3.5, aspect=1.5)
grid = sns.FacetGrid(hue='y', data=df, aspect=5)
grid.map(sns.kdeplot, nom)
grid.add_legend()

# <2.2  >5  >9 >9.3  >11  <8.5  >11 >11 >13 >550

In [ ]:
# seuils de transition : à choisir 
s = np.array([0.2,0.3]) 
bins = [df[nom].min(), s[0], s[1], df[nom].max()]
df['top_x1'] = pd.cut(x=df[nom], bins=bins, include_lowest=True, 
                      labels=["P", "M", "G"])
dum = pd.get_dummies(df[['top_x1']])

- Jouer avec les seuils de transitions ==> refaire tourner cette étape pluieurs fois en observant les profils associés

In [ ]:
df.head()

In [ ]:
dum.head()

In [ ]:
# Etude des profils
pd.crosstab(df['y'], df['top_x1'], normalize='columns')

### Exercice
- Que vaut la somme de chaque colonne ? 
- Comparons chacun des 3 profils au profil moyen de la population 

In [ ]:
# profil moyen
print("Rappelons la valeur du taux de cible: {taux:.2f}%".format(taux = tx_cible))

Une *bonne* méthode pour discrétiser une variable quantitative dans l'objectif de maximiser l'impact des tranches sur la cible consiste en

- choisir un découpage qui maximise l'écart au comportement moyen de la population sur la cible 
- ne pas garder les tranches qui se comportent comme l'ensemble de la population 

**Ici, quels profils gardons nous ?**

In [ ]:
print("Vérifions que les effectifs ne sont pas trop petits")
print(pd.crosstab(dum['top_x1_P'], df['y']))


Lorsqu'on a beaucoup de données, on peut créer beaucoup de dummies en créant des tranches de manière automatique ==> par exemple en utilisant les quantiles.

In [ ]:
# calculer les déciles de toutes les quanti
s = quanti.quantile(np.linspace(0, 1., 11))
s

### Exercice

1. En utilisant les fonctions pd.cut, pd.get_dummies, créez un dataframe contenant toutes les variables quanti
"dummifiées", en utilisant les 10 quantiles calculés dans `s` pour chaque colonne. On n'oubliera pas de `drop_first=True`...

1. Puis rajouter les variables `quali` dans le tableau

1. Et sauvegarder le tout avec `pickle` (comme avant)

### Solution 1.

In [ ]:
labels = ["Q1", "Q2", "Q3", "Q4", "Q5", "Q6", "Q7", "Q8", "Q9", "Q10"]

cats = [
    pd.cut(col, bins=s[nom], labels=labels, include_lowest=True)
    for nom, col in quanti.items()    
]

cats = pd.concat(cats, axis=1)

dum0 = pd.get_dummies(cats, drop_first=True)
dum0.head()

### Solution 2.

In [ ]:
quali.head()

In [ ]:
df_trav = pd.concat([dum0, pd.get_dummies(quali, drop_first=True)], axis=1)
df_trav.head()

### Solution 3.

In [ ]:
# Sauver
with open(os.path.join(path_travail, 'df_dumAll.pkl'), 'wb') as f:
    pkl.dump({'features': df_trav, 'labels': defaut}, f)

# Questions que l'on se pose

- Un codage 'bête' des qualitatives est-il performant ?
- A-t-on besoin de réduire les quantitatives ? 
- Est-ce mieux de travailler uniquement avec des dummies ? 

On va répondre à ces questions en utilisant les quatre bases de travail que l'on vient de créer : 

- `df_brut`
- `df_dum0`
- `df_dum0N`
- `df_dumAll`

<a id='model'></a>
# 3. Modélisation 

Le modèle proposé est la **régression logistique**; les méthodologies à challenger sont

- sélection de variables "à la main"
- pénalisation L1 du modèle avec paramètre tunné par défaut
- pénalisation L1 du modèle avec paramètre tunné par validation croisée


La modélisation se fait en trois temps :
- on sépare les données : LEARN / TEST
- on apprend le modèle 
- on ré-applique le modèle

**On commence à travailler avec la base `df_brut`**

# 3.1. Split des données

Avec le même taux de cible : base LEARN = 70% et base test = 30%

In [ ]:
from sklearn.model_selection import train_test_split

# Chargement base de travail
with open(os.path.join(path_travail, 'df_brut.pkl'), 'rb') as f:
    data = pkl.load(f)
    
X, y = data['features'], data['labels']
features_names = X.columns.tolist()

In [ ]:
print(X.shape, y.shape)
print(features_names)

In [ ]:
# split TRAIN / TEST
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=15)

In [ ]:
X_train.head()

### Exercice

- Calculez le pourcentage de labels 1 dans le train et le test (pour vérifier que c'est bien le même)

### Solution

In [ ]:
pd.concat([
    pd.DataFrame({'y': y_train, 'dataset': 'train'}),
    pd.DataFrame({'y': y_test, 'dataset': 'test'})
]).groupby('dataset').agg(['count', 'sum', 'mean'])

On observe que le pourcentage de 1 n'est pas tout à fait le même ==>  on utilise l'option * stratify=y* qui opère une stratification par rapport à y

In [ ]:
# split TRAIN / TEST
X_train, X_test, y_train, y_test = train_test_split(X, y, stratify=y, test_size=0.3, random_state=15)

### Exercice

- Re-Calculez le pourcentage de labels 1 dans le train et le test

# 3. 2. Modèle logistique avec séléction "à la main"

Critères de choix : 
- on garde les plus corrélées à la cible pour construire un premier modèle
- on se concentre sur les variables significatives
                 
résultats de scores 
- dans pred_train, pred_test    

In [ ]:
# Sélection de variables préalable : les plus corrélées à la cible
from scipy.stats.stats import pearsonr

correlations = X_train.apply(
    lambda col: pearsonr(col, y_train), 
    axis=0, result_type='expand',
)

correlations.index = ['Correlation', 'p_value']
correlations

### Exercice
- Lorsqu'on teste la nullité d'une corrélation, que signifie la p-value associée au test ? 
- La variable $x1$ semble-t-elle intéressante pour expliquer $Y$ ? Et $x9$ ?
- Plus généralement, quelles variables garder ?

In [ ]:
p_values = correlations.loc['p_value'].sort_values(ascending=True)
p_values

In [ ]:
var_keep = p_values.index.tolist()[:7]
var_keep

In [ ]:
import statsmodels.api as sm

X0_train = X_train.loc[:, var_keep]
y0_train = y_train

logreg = sm.Logit(y0_train, X0_train)
result = logreg.fit()

# Resultats de la regression logistique
result.summary()

### Exercice
- Les variables sont-elles toutes significatives ? Lesquelles garder ?

In [ ]:
var_keep = ['x7', 'x10', 'x8', 'x5', 'x3', 'x4']

X0_train = X_train[var_keep]
X0_test =  X_test[var_keep]
y0_train = y_train 
y0_test = y_test

logreg = sm.Logit(y0_train,X0_train )
result = logreg.fit()
result.summary()

In [ ]:
import matplotlib.pyplot as plt

# Re-application sur les bases TRAIN et TEST 
pred_test = pd.concat([y0_test, result.predict(X0_test)], axis=1)
pred_test.rename(columns={0:'score'}, inplace=True)
pred_test = pred_test.sort_values(by='score', ascending=False) 

pred_train = pd.concat([y0_train, result.predict(X0_train)], axis=1) 
pred_train.rename(columns={0:'score'}, inplace=True)
pred_train = pred_train.sort_values(by='score', ascending=False) 

# Courbes de scores 
plt.subplot(2, 1, 1)
x = np.linspace(0, 1, len(pred_test.score))
print(x.shape[0])
plt.plot(x, pred_test.score, linewidth=2, color='r') 

plt.subplot(2, 1, 2)
x = np.linspace(0, 1, len(pred_train.score))
print(x.shape[0])
plt.plot(x, pred_train.score, linewidth=2, color='g') 

In [ ]:
# Sauver les scores pour df_brut
pred_test_brut = pred_test
pred_train_brut = pred_train

# 3.3. Modélisation logistique avec sélection automatique des variables 

On utilise une pénalité L1 des coefficients avec choix optimisé de la constante de pénalisation

In [ ]:
# Modèle avec pénalisation L1 <== tunning par défaut

from sklearn.linear_model import LogisticRegression, LogisticRegressionCV

logreg = LogisticRegression(penalty='l1', solver='liblinear')  # définition du modèle
logreg.fit(X_train, y_train)                      # apprentissage
res_test = logreg.predict_proba(X_test)           # ré-application
res_train = logreg.predict_proba(X_train)         # ré-application

# Affichage
temp = pd.Series(res_test[:, 1], index=y_test.index)
pred_test = pd.concat([y_test, temp], axis=1)
pred_test.rename(columns={0: 'score'}, inplace=True)
pred_test = pred_test.sort_values(by='score', ascending=False) 

temp = pd.Series(res_train[:, 1], index=y_train.index)
pred_train = pd.concat([y_train, temp], axis=1) 
pred_train.rename(columns={0: 'score'}, inplace=True)
pred_train = pred_train.sort_values(by = 'score', ascending = False) 

# Courbes de scores 
plt.subplot(2, 1, 1)
x = np.linspace(0, 1, len(pred_test.score))
print(len(x))
plt.plot(x,pred_test.score, linewidth=2, color='r') 

plt.subplot(2, 1, 2)
x = np.linspace(0, 1, len(pred_train.score))
print(len(x))
plt.plot(x,pred_train.score, linewidth=2, color='g') 

# Sauver les scores pour df_brut pénalisation par defaut
pred_test_brut_pen0 = pred_test;pred_train_brut_pen0 = pred_train;

In [ ]:
# Visualisation des coefficients 
logreg.coef_

In [ ]:
logreg.intercept_

In [ ]:
plt.figure(figsize=(14, 4))
plt.stem(logreg.coef_.ravel(), use_line_collection=True)
plt.title('Logistic regression coefficients', fontsize=16)
# We change the fontsize of minor ticks label
_ = plt.xticks(np.arange(logreg.coef_[0].shape[0]), features_names,
           rotation='vertical', fontsize=12)
_ = plt.yticks(fontsize=14)

### Exercice
- Comment expliquer le coefficient de $x7$ ? (ref code [17]) 
- cela implique-t-il de mauvaises performances ??

In [ ]:
# Tuning de C (modèle avec pénalisation L1)
c_path = np.logspace(-4, 2, 10)
# c_path plus long ==> durée calcul plus longue
print(c_path) 

In [ ]:
# Tuning de C 
logreg = LogisticRegression(penalty='l1', tol=1e-4, solver='liblinear')
coeffs = []
for c in c_path:
    logreg.C = c
    logreg.fit(X_train, y_train)
    coeffs.append(logreg.coef_.ravel().copy())

coeffs = np.array(coeffs)
plt.figure(figsize=(10, 8))
plt.semilogx(c_path, coeffs)
ymin, ymax = plt.ylim()
plt.xlabel('C', fontsize=16)
plt.xticks(fontsize=14)
plt.ylabel('Coefficients', fontsize=16)
plt.yticks(fontsize=14)
plt.title('Evolution de chaque coef de la logistique '
          'avec la penalisation L1', fontsize=16)

plt.show()

### Exercice
- A votre avis, de quels coefficients les courbes rose/bleue montrent-elles l'évolution ?
- Sur quelle grille faire varier C pour optimisation ?

## Logistique pénalisée avec paramètre de pénalisation optimisé

### Exercice
- Remplacer les ??? par des valeurs 

In [ ]:
# Validation croisee validation croisée pour le choix automatique de C
# resultats intermédiares de calculs d'erreurs
logreg_cv = LogisticRegressionCV(penalty='l1',
                                 tol=1e-3,
                                 Cs=np.logspace(-3, 5, 15),
                                 cv=3,
                                 solver='liblinear',
                                 # class_weight='balanced',
                                 scoring='roc_auc')

logreg_cv.fit(X_train, y_train)
err = logreg_cv.scores_[1]
print(err)

In [ ]:
# Validation croisee validation croisée pour le choix automatique de C
# resultats intermédiares menant au choix de C optimal
score_boot = err.mean(axis=0)
print(score_boot)
C_opt = logreg_cv.C_[0]
print("C optimale =", C_opt)

In [ ]:
plt.plot(score_boot)

In [ ]:
# Apprentissage avec le bon tuning et réapplication 
CC = 0.01  # sous-optimale
#CC = C_opt
logreg = LogisticRegression(penalty='l1', C=CC, solver='liblinear')
logreg.fit(X_train, y_train)
res_test = logreg.predict_proba(X_test)
res_train = logreg.predict_proba(X_train)

temp = pd.Series(res_test[:, 1], index = y_test.index)
pred_test = pd.concat([y_test, temp], axis=1)
pred_test.rename(columns={0: 'score'}, inplace=True)
pred_test = pred_test.sort_values(by='score', ascending=False) 

temp = pd.Series(res_train[:, 1], index=y_train.index)
pred_train = pd.concat([y_train,temp], axis=1) 
pred_train.rename(columns={0: 'score'}, inplace=True)
pred_train = pred_train.sort_values(by='score', ascending=False) 

# Sauver les scores pour df_brut pénalisation par defaut
pred_test_brut_pen = pred_test
pred_train_brut_pen = pred_train

<a id='perf'></a>
# 3. PERFORMANCES

La performance s'analyse sur la base TEST

- Courbe ROC
- Indices AUC / Gini

Il est utile de comparer les courbes ROC calculées avec la base TEST versus la base TRAIN pour détecter un sur-apprentissage potentiel

In [ ]:
from sklearn.metrics import roc_curve, auc, precision_recall_curve, f1_score

# Performance ROC pour les différentes stratégies sur TEST
plt.figure(figsize=(7, 6))
plt.plot([0, 1], [0, 1], 'k--')

fpr, tpr, _ = roc_curve(pred_test_brut.y, pred_test_brut.score)
plt.plot(fpr, tpr, label="Data Brut + Selec manuelle (AUC=%.2f)" % auc(fpr, tpr), lw=2)
plt.legend(loc="lower right", fontsize=10)

plt.xlim([0.0, 1.0])
plt.ylim([0.0, 1.05])
plt.xlabel('False Positive Rate', fontsize=16)
plt.ylabel('True Positive Rate', fontsize=16)
plt.title('Receiver operating characteristic', fontsize=18)
plt.legend(loc="lower right", fontsize=10)

fpr, tpr, _ = roc_curve(pred_test_brut_pen0.y, pred_test_brut_pen0.score)
plt.plot(fpr, tpr, label="Data Brut + Penalisation par defaut  (AUC=%.2f)" % auc(fpr, tpr), lw=2)
plt.legend(loc="lower right", fontsize=10)

fpr, tpr, _ = roc_curve(pred_test_brut_pen.y, pred_test_brut_pen.score)
plt.plot(fpr, tpr, label="Data Brut + Penalisation choisie (AUC=%.2f)" % auc(fpr, tpr), lw=2)
plt.legend(loc="lower right", fontsize=10)

### Exercice
- Que penser de la pénalité proposée par défaut par Python ?

In [ ]:
# Performance ROC pour TRAIN et TEST == Sur Apprentissage ??

pred_test = pred_test_brut_pen0
pred_train = pred_train_brut_pen0

# TRAIN et TEST
plt.figure(figsize=(7, 6))

fpr, tpr, _ = roc_curve(pred_test.y, pred_test.score)
plt.plot([0, 1], [0, 1], 'k--')
plt.plot(fpr, tpr, label="Test (AUC=%.2f)" % auc(fpr, tpr), lw=2)
plt.xlim([0.0, 1.0])
plt.ylim([0.0, 1.05])
plt.xlabel('False Positive Rate', fontsize=16)
plt.ylabel('True Positive Rate', fontsize=16)
plt.title('Receiver operating characteristic', fontsize=18)
plt.legend(loc="lower right", fontsize=16)

fpr, tpr, _ = roc_curve(pred_train.y, pred_train.score)
plt.plot(fpr, tpr, label="Train (AUC=%.2f)" % auc(fpr, tpr), lw=2)
plt.legend(loc="lower right", fontsize=16)

### Exercice
- Avec quelle base a-t-on le meilleur résultat ? Etait ce attendu ?
- Peut-on penser qu'on n'est pas en situation de sur-apprentissage ?


# 4. Conclusion

Lorsque la modélisation convient, on la sauve (de manière à ne pas à refaire l'apprentissage qui peut être long)

In [ ]:
# sauvegarder le modele dans un fichier 'logreg.pkl'
import pickle as pkl

path_modeles = './'
with open('logreg.pkl', 'wb') as f:
    pkl.dump(logreg, f)

In [ ]:
# charger le modèle
import pickle as pkl

path_modeles = './'

with open('logreg.pkl', 'rb') as f:
    modele = pkl.load(f)

# 5. A faire

Entrainez des regressions logistiques et chercher un meilleur modele pour les trois autres bases :

- `df_dum`
- `df_dumN`
- `df_dumAll`

Comparez toutes les courbes ROC obtenues ==> Conclusion ?